In [0]:
//If using Apache Toree dependency
%AddDeps org.vegas-viz vegas_2.11 0.3.11 --transitive

(console):2:35 expected (Semis | &"}" | end-of-input)
%AddDeps org.vegas-viz vegas_2.11 0.3.11 --transitive
                                  ^

: 

In [0]:
//If using Apache Toree dependency
implicit val render = vegas.render.ShowHTML(kernel.display.content("text/html", _))

cmd0.sc:1: not found: value vegas
implicit val render = vegas.render.ShowHTML(kernel.display.content("text/html", _))
                      ^cmd0.sc:1: value display is not a member of almond.api.FullJupyterApi
 Note: implicit value render is not applicable here because it comes after the application point and it lacks an explicit result type
implicit val render = vegas.render.ShowHTML(kernel.display.content("text/html", _))
                                                   ^Compilation Failed

: 

In [1]:
//If using Almond dependency
import $ivy.`org.vegas-viz::vegas:0.3.11`

import $ivy.$                            

# Data Exploration with Functional Programming using Jupyter Notebook, Scala and Vegas
## A Statistical Analysis of the Titanic Dataset

Titanic survivor dataset captures the various details of people who survived or not survived in the shipwreck. Using this data, we want to build a model which predicts the propability of someone's survival. It is a classification problem that maps all attributes like sex, fare, age on the most probable state: Survived or not

![Titanic](Titanic.jpg)
(Source: https://commons.wikimedia.org/wiki/RMS_Titanic)


The dataset contains the following attributes (for more information: see Kaggle):

| **Variable** | **Definition**                                | **Key**                                           |
|--------------|-----------------------------------------------|---------------------------------------------------|
| survival     | Survival                                      | 1=Yes, 0= No                                      |
| pclass       | Ticket class                                  | 1 = 1st, 2 = 2nd, 3 = 3rd                         |
| sex          | Sex                                           |                                                   |
| age          | Age                                           | Age in years                                      |
| sibsp        |  # of siblings / spouses aboard   the Titanic |                                                   |
| parch        |  # of parents / children aboard   the Titanic |                                                   |
| ticket       | Ticket number                                 |                                                   |
| fare         | Passenger fare                                |                                                   |
| cabin        | Cabin number                                  |                                                   |
| embarked     | Port of Embarkation                           |  C = Cherbourg, Q = Queenstown,   S = Southampton |


The dataset is splittet into three files:
* A Training Dataset (train.csv)
* A Test Dataset (test.csv)
* A Set which contains sample data for the submission (gender_submission.csv).

At first, we need to load the data creating maps for each set.

In [2]:
import vegas._
import vegas.data.External._
import java.io.PrintWriter
import scala.util.Try

// Regular Expressions for extracting the information
val DATA_ACCESS_PATTERN_test = """(\d+),(\d),"(.+)",(male|female),([0-9]*\.[0-9]+|[0-9]+|d*),(\d*),(\d*),(.*),([0-9]*\.[0-9]+|[0-9]+|d*),(.*),(\w*)""".r
val DATA_ACCESS_PATTERN_train=  """(\d+),(\d),(\d),"(.+)",(male|female),([0-9]*\.[0-9]+|[0-9]+|d*),(\d*),(\d*),(.*),([0-9]*\.[0-9]+|[0-9]+|d*),(.*),(\w*)""".r

// Reading text file
// Stores the information in a map consisting of a property name (key) and its value
def loadDataCSV(filename:String):List[Map[String,Any]]= {

  val src = scala.io.Source.fromFile(filename)
  val iter = src.getLines().drop(1) //skip first line (property names)
    
    val result= (for (row <- iter) yield readData(row)).toList
   
    src.close
    result.flatMap(_ match{ case p:Option[Map[String,Any]]=>p})
}
  

// Extracting all information storing it into a Map[String,Any]
def readData(line:String):Option[Map[String,Any]]={
    
    def toInt(key: String, s: String): Option[(String, Int)] = Try(s.toInt).toOption.map((key, _))

    def toFloat(key: String, s: String): Option[(String, Float)] = Try(s.toFloat).toOption.map((key, _))
  
    def toString(key:String, s:String):Option[(String,String)]=
        if (s.nonEmpty) Some((key,s)) else None

    def createPassengerMap(t1:String,t2:String,t3:String,t4:String,t5:String,t6:String,t7:String,
                           t8:String,t9:String,t10:String,t11:String,t12:String):Option[Map[String,Any]]={
        
        val l=List(
            toInt("passengerID",t1),
            toInt("survived",t2),
            toInt("pclass",t3),
            toString("name",t4),
            toString("sex",t5),
            toFloat("age",t6),
            toInt("sibsp",t7),
            toInt("parch",t8),
            toString("ticket",t9),
            toFloat("fare",t10),
            toString("cabin",t11),
            {if (t12.length>0) Some(("embarked",t12(0))) else None})
         Some(l.flatMap(_ match{ case p:Option[(String,Any)]=>p}).toMap)        
    }
    
    val result = line match{
       case DATA_ACCESS_PATTERN_test(t1,t3,t4,t5,t6,t7,t8,t9,t10,t11,t12) => 
                 createPassengerMap(t1,"-1",t3,t4,t5,t6,t7,t8,t9,t10,t11,t12)
       
       case DATA_ACCESS_PATTERN_train(t1,t2,t3,t4,t5,t6,t7,t8,t9,t10,t11,t12) => {
                  createPassengerMap(t1,t2,t3,t4,t5,t6,t7,t8,t9,t10,t11,t12)
       }
       
     }
     result
}

// Method for printing a passenger in a readable manner
def printPassenger(p:Map[String,Any]):Unit={
    
    println("\n---------------------------------------------------------------------")
    println("passengerID:"+p.getOrElse("passengerID",-1))
    println("survived:"+p.getOrElse("survived",-1))
    println("pclass:"+p.getOrElse("pclass",-1))
    println("name:"+p.getOrElse("name","-"))
    println("sex:"+p.getOrElse("sex","-"))
    println("age:"+p.getOrElse("age",-1))
    println("sibsp:"+p.getOrElse("sibsp",-1))
    println("parch:"+p.getOrElse("parch",-1))
    println("ticket:"+p.getOrElse("ticket","-"))
    println("fare:"+p.getOrElse("fare",-1))
    println("cabin:"+p.getOrElse("cabin",-1))
    println("embarked:"+p.getOrElse("embarked",'-'))
    println("---------------------------------------------------------------------\n")
}
  
//produces sometimes an missing argument list error - can be ignored
def applyModel[CLASS,ID](model:(Map[String,Any],String)=> (ID,CLASS), 
            testdata: Seq[Map[String,Any]], idKey:String):Seq[(ID,CLASS)]= {
    
    testdata.map(d => model(d,idKey))
}  

def createSubmitFile[ID,CLASS](filename:String, data:Seq[(ID,CLASS)],header:String):Unit= {
    val pw = new PrintWriter(filename)
    pw.println(header)
    data.foreach(e=>pw.println(e._1.toString+","+e._2.toString))
    pw.close
}

import vegas._

import vegas.data.External._

import java.io.PrintWriter

import scala.util.Try

// Regular Expressions for extracting the information

DATA_ACCESS_PATTERN_test: scala.util.matching.Regex = (\d+),(\d),"(.+)",(male|female),([0-9]*\.[0-9]+|[0-9]+|d*),(\d*),(\d*),(.*),([0-9]*\.[0-9]+|[0-9]+|d*),(.*),(\w*)
DATA_ACCESS_PATTERN_train: scala.util.matching.Regex = (\d+),(\d),(\d),"(.+)",(male|female),([0-9]*\.[0-9]+|[0-9]+|d*),(\d*),(\d*),(.*),([0-9]*\.[0-9]+|[0-9]+|d*),(.*),(\w*)
defined function loadDataCSV
defined function readData
defined function printPassenger
defined function applyModel
defined function createSubmitFile

In [3]:
val train= loadDataCSV("train.csv")
val test= loadDataCSV("test.csv")
val all= train ++ test
  
println("Train Dataset:"+ train.size+" Elements")
println("Test Dataset:"+ test.size+" Elements")
println("Whole Dataset:"+ all.size+" Elements")


Train Dataset:891 Elements
Test Dataset:418 Elements
Whole Dataset:1309 Elements


train: List[Map[String, Any]] = List(
  Map(
    "name" -> "Braund, Mr. Owen Harris",
    "fare" -> 7.25F,
    "parch" -> 0,
    "age" -> 22.0F,
    "ticket" -> "A/5 21171",
    "sex" -> "male",
    "passengerID" -> 1,
    "pclass" -> 3,
    "sibsp" -> 1,
    "embarked" -> 'S',
    "survived" -> 0
  ),
  Map(
    "name" -> "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
    "fare" -> 71.2833F,
    "parch" -> 0,
    "age" -> 38.0F,
    "ticket" -> "PC 17599",
    "cabin" -> "C85",
    "sex" -> "female",
    "passengerID" -> 2,
    "pclass" -> 1,
    "sibsp" -> 1,
    "embarked" -> 'C',
    "survived" -> 1
  ),
  Map(
    "name" -> "Heikkinen, Miss. Laina",
    "fare" -> 7.925F,
    "parch" -> 0,
    "age" -> 26.0F,
    "ticket" -> "STON/O2. 3101282",
    "sex" -> "female",
    "passengerID" -> 3,
    "pclass" -> 3,
    "sibsp" -> 0,
    "embarked" -> 'S',
...
test: List[Map[String, Any]] = List(
  Map(
    "name" -> "Kelly, Mr. James",
    "fare" -> 7.8292F,
    "parch" -> 0,
   

Now we can examine a small sample of the data set

In [4]:
all.take(2).foreach(printPassenger)


---------------------------------------------------------------------
passengerID:1
survived:0
pclass:3
name:Braund, Mr. Owen Harris
sex:male
age:22.0
sibsp:1
parch:0
ticket:A/5 21171
fare:7.25
cabin:-1
embarked:S
---------------------------------------------------------------------


---------------------------------------------------------------------
passengerID:2
survived:1
pclass:1
name:Cumings, Mrs. John Bradley (Florence Briggs Thayer)
sex:female
age:38.0
sibsp:1
parch:0
ticket:PC 17599
fare:71.2833
cabin:C85
embarked:C
---------------------------------------------------------------------



Count the missing values in a passenger set.

In [5]:
val attList= List("passengerID","pclass","survived","name","sex","age","sibsp","parch",
        "ticket","fare","cabin","embarked")

def countAllMissingValues(data:List[Map[String,Any]],attList:List[String]):Map[String,Int]= {
     def mapReduce[S,B,R](mapFunc:S=>List[B], redFunc:(R,B)=> R, base:R, list: List[S]):R ={
      list.flatMap(mapFunc).foldLeft[R](base)(redFunc)
    }

    val list = mapReduce[Map[String, Any], (String, Int), Map[String, Int]](
      x=> x.map(y=> (y._1, 1)).toList,
      (map, x) => map.updated(x._1, x._2 + map.getOrElse(x._1, 0)),
      Map():Map[String, Int], data
    )

    list.map(x=> (x._1, data.length-x._2))
}  

val train_mv= countAllMissingValues(train,attList)
val test_mv= countAllMissingValues(test,attList)
assert(train_mv("cabin")== 687 && train_mv("age")==177 && train_mv("embarked")== 2)
assert(test_mv("cabin")== 327 && test_mv("age")==86 && test_mv("fare")== 1)

attList: List[String] = List(
  "passengerID",
  "pclass",
  "survived",
  "name",
  "sex",
  "age",
  "sibsp",
  "parch",
  "ticket",
  "fare",
  "cabin",
  "embarked"
)
defined function countAllMissingValues
train_mv: Map[String, Int] = Map(
  "name" -> 0,
  "fare" -> 0,
  "parch" -> 0,
  "age" -> 177,
  "ticket" -> 0,
  "cabin" -> 687,
  "sex" -> 0,
  "passengerID" -> 0,
  "pclass" -> 0,
  "sibsp" -> 0,
  "embarked" -> 2,
  "survived" -> 0
)
test_mv: Map[String, Int] = Map(
  "name" -> 0,
  "fare" -> 1,
  "parch" -> 0,
  "age" -> 86,
  "ticket" -> 0,
  "cabin" -> 327,
  "sex" -> 0,
  "passengerID" -> 0,
  "pclass" -> 0,
  "sibsp" -> 0,
  "embarked" -> 0,
  "survived" -> 0
)

In [6]:
Vegas("Passengers split by sex" ).
    withData(train).
    mark(Bar).
    encodeX("sex", Ordinal,axis=Axis(title="Sex")).
    encodeY("passengerID", Quantitative,AggOps.Count,axis=Axis(title="Passengers")).
    show

<iframe id="frame-vegas-8d59fda9-b3de-4fc3-a74d-41dedfcf34ea" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-8d59fda9-b3de-4fc3-a74d-41dedfcf34ea'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "axis" : {
 "title" : "Sex"
 },
 "field" : "sex",
 "type" : "ordinal"
 },
 "y" : {
 "axis" : {
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 }
 },
 "description" : "Passengers split by sex",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783",
 "cabin" : "C103",
 "sex" : "female",
 "passengerID" : 12,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Saundercock, Mr. William Henry",
 "f

In [7]:
val passengers= train.size
val survivedPass= (train.filter(m=>m("survived")==1)).size
val rate= survivedPass.toDouble/passengers
println("propability of surviving:"+rate)

Vegas("Passengers classified by survival" ).
    withData(train).
    mark(Bar).
    addTransform("survival", "datum.survived == 0 ? \"Dead\" : \"Alive\"").
    encodeX("survival", Ordinal,axis=Axis(title="Survival")).
    encodeY("passengerID", Quantitative,AggOps.Count,axis=Axis(title="Passengers")).show

propability of surviving:0.3838383838383838


<iframe id="frame-vegas-2c26fcd6-c78b-44a3-8bd5-784c92c54c32" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-2c26fcd6-c78b-44a3-8bd5-784c92c54c32'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "axis" : {
 "title" : "Survival"
 },
 "field" : "survival",
 "type" : "ordinal"
 },
 "y" : {
 "axis" : {
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 }
 },
 "description" : "Passengers classified by survival",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783",
 "cabin" : "C103",
 "sex" : "female",
 "passengerID" : 12,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Saundercock, Mr.

passengers: Int = 891
survivedPass: Int = 342
rate: Double = 0.3838383838383838

In [8]:
Vegas("Survival split by sex").
      withData(train).
      mark(Bar).
      addTransform("survival", "datum.survived == 0 ? \"No\" : \"Yes\"").
      encodeY("passengerID",Quantitative, AggOps.Count, axis=Axis(title="Passengers")).
      encodeX("sex", Ord).
      encodeColor("survival", Nominal, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA"))).
      show

<iframe id="frame-vegas-ffa6975b-9aab-4b8d-8f37-f7c64b31a8e7" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-ffa6975b-9aab-4b8d-8f37-f7c64b31a8e7'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "sex",
 "type" : "ordinal"
 },
 "y" : {
 "axis" : {
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "survival",
 "type" : "nominal"
 }
 },
 "description" : "Survival split by sex",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783",
 "cabin" : "C103",
 "sex" : "female",
 "passengerID" : 12,
 "pclass" : 1,
 "sibsp" : 0,
 "embark

In [9]:
Vegas("Survival split by sex").
      withData(train).
      mark(Bar).
      addTransform("survival", "datum.survived == 0 ? \"No\" : \"Yes\"").
      encodeY("passengerID",Quantitative, AggOps.Count, axis=Axis(title="Passengers",format="s")).
      encodeX("sex", Ord).
      encodeColor("survival", Nominal, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA"))).
      configMark(stacked = StackOffset.Normalize).
      show

<iframe id="frame-vegas-0d018497-d693-432c-88fc-a1983ac756c7" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-0d018497-d693-432c-88fc-a1983ac756c7'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "sex",
 "type" : "ordinal"
 },
 "y" : {
 "axis" : {
 "format" : "s",
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "survival",
 "type" : "nominal"
 }
 },
 "description" : "Survival split by sex",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783",
 "cabin" : "C103",
 "sex" : "female",
 "passengerID" : 12,
 "pclass" : 1,
 "sib

In [10]:
Vegas("Age Distribution of all Passengers").
    withData(train).
    mark(Bar).
    addTransformCalculation("age","datum.age-(datum.age % 10)").
    encodeX("age", dataType= Nominal,scale=Scale(bandSize=20.0)).
    encodeY("passengerID", Quant ,AggOps.Count, axis=Axis(title="Passengers")).
    show

<iframe id="frame-vegas-88baa7cd-13bf-4309-a4f6-9253782500cb" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-88baa7cd-13bf-4309-a4f6-9253782500cb'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "scale" : {
 "bandSize" : 20.0
 },
 "field" : "age",
 "type" : "nominal"
 },
 "y" : {
 "axis" : {
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 }
 },
 "description" : "Age Distribution of all Passengers",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783",
 "cabin" : "C103",
 "sex" : "female",
 "passengerID" : 12,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Saundercock, Mr. Willi

In [11]:
Vegas("Age Distribution splitted by Survival").
    withData(train).
    addTransform("survival", "datum.survived == 0 ? \"No\" : \"Yes\"").
    mark(Bar).
    encodeX("age", Quant, bin=Bin(step=10.0,min= 0.0),axis=Axis(title="Age")).
    encodeY("passengerID", Quantitative ,AggOps.Count,axis=Axis(title="Passengers")).
    encodeColor("survival", Nominal, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA"))).
    show

<iframe id="frame-vegas-fe70bff0-c353-4c35-9a0b-a974b0026cf5" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-fe70bff0-c353-4c35-9a0b-a974b0026cf5'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "axis" : {
 "title" : "Age"
 },
 "field" : "age",
 "type" : "quantitative",
 "bin" : {
 "min" : 0.0,
 "step" : 10.0
 }
 },
 "y" : {
 "axis" : {
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "survival",
 "type" : "nominal"
 }
 },
 "description" : "Age Distribution splitted by Survival",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783"

In [12]:
Vegas("Age Distribution splitted by Survival").
    withData(train).
    addTransform("survivad", "datum.survived == 0 ? \"No\" : \"Yes\"").
    addTransform("Age Description", "datum.age <= 4 ? \"1-Infant\" : datum.age<=15 ? \"2-Child\" : datum.age<=50 ? \"3-Adult\" : \"4-Old\"").
    mark(Bar).
    encodeX("Age Description", Ordinal).
    encodeY("passengerID", Quantitative ,AggOps.Count,axis=Axis(title="Passengers")).
    encodeColor("survival", Nominal, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA"))).
    show

<iframe id="frame-vegas-3d25f655-7072-437f-bb75-9b226f229c96" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-3d25f655-7072-437f-bb75-9b226f229c96'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "Age Description",
 "type" : "ordinal"
 },
 "y" : {
 "axis" : {
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "survival",
 "type" : "nominal"
 }
 },
 "description" : "Age Distribution splitted by Survival",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783",
 "cabin" : "C103",
 "sex" : "female",
 "passengerID" : 12,
 "pclass"

In [13]:
Vegas("die Ueberlebensrate nach Alter").
    withData(train).
    addTransform("survived", "datum.survived == 0 ? \"No\" : \"Yes\"").
    mark(Bar).
    encodeX("age", Quant, bin=Bin(step=10.0,min= 0.0),axis=Axis(title="Age")).
    encodeY("passengerID", Quantitative ,AggOps.Count,axis=Axis(title="Passengers", format="s")).
    encodeColor("survived", Nominal, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA"))).
    configMark(stacked = StackOffset.Normalize).
    show

<iframe id="frame-vegas-c9237247-1306-4a23-913f-17224a1eaf67" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-c9237247-1306-4a23-913f-17224a1eaf67'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "axis" : {
 "title" : "Age"
 },
 "field" : "age",
 "type" : "quantitative",
 "bin" : {
 "min" : 0.0,
 "step" : 10.0
 }
 },
 "y" : {
 "axis" : {
 "format" : "s",
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "survived",
 "type" : "nominal"
 }
 },
 "description" : "die Ueberlebensrate nach Alter",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" 

In [14]:
Vegas("die Ueberlebensrate nach Passagierklasse").
    withData(train).
    addTransform("survived", "datum.survived == 0 ? \"No\" : \"Yes\"").
    mark(Bar).
    encodeX("pclass", Ord).
    encodeY("passengerID", Quantitative ,AggOps.Count,axis=Axis(title="Passengers" , format="s")).
    encodeColor("survived", Nominal, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA"))).
    configMark(stacked = StackOffset.Normalize).
    show

<iframe id="frame-vegas-0b0dbde5-40af-4323-a263-0c1e4885c7d7" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-0b0dbde5-40af-4323-a263-0c1e4885c7d7'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "pclass",
 "type" : "ordinal"
 },
 "y" : {
 "axis" : {
 "format" : "s",
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "survived",
 "type" : "nominal"
 }
 },
 "description" : "die Ueberlebensrate nach Passagierklasse",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783",
 "cabin" : "C103",
 "sex" : "female",
 "passengerID" : 12

In [15]:
Vegas("die Ueberlebensrate nach Hafen").
    withData(train).
    addTransform("survived", "datum.survived == 0 ? \"No\" : \"Yes\"").
    mark(Bar).
    encodeX("embarked", Ord).
    encodeY("passengerID", Quantitative ,AggOps.Count,axis=Axis(title="Passengers" , format="s")).
    encodeColor("survived", Nominal, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA"))).
    configMark(stacked = StackOffset.Normalize).
    show

<iframe id="frame-vegas-9c99ac27-e43f-40fa-b7db-4c4cf102a2fa" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-9c99ac27-e43f-40fa-b7db-4c4cf102a2fa'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "embarked",
 "type" : "ordinal"
 },
 "y" : {
 "axis" : {
 "format" : "s",
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "survived",
 "type" : "nominal"
 }
 },
 "description" : "die Ueberlebensrate nach Hafen",
 "data" : {
 "values" : [
 {
 "name" : "Braund, Mr. Owen Harris",
 "fare" : 7.25,
 "parch" : 0,
 "age" : 22.0,
 "ticket" : "A/5 21171",
 "sex" : "male",
 "passengerID" : 1,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
 "fare" : 71.2833023071289,
 "parch" : 0,
 "age" : 38.0,
 "ticket" : "PC 17599",
 "cabin" : "C85",
 "sex" : "female",
 "passengerID" : 2,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Heikkinen, Miss. Laina",
 "fare" : 7.925000190734863,
 "parch" : 0,
 "age" : 26.0,
 "ticket" : "STON/O2. 3101282",
 "sex" : "female",
 "passengerID" : 3,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Futrelle, Mrs. Jacques Heath (Lily May Peel)",
 "fare" : 53.099998474121094,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "113803",
 "cabin" : "C123",
 "sex" : "female",
 "passengerID" : 4,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allen, Mr. William Henry",
 "fare" : 8.050000190734863,
 "parch" : 0,
 "age" : 35.0,
 "ticket" : "373450",
 "sex" : "male",
 "passengerID" : 5,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Moran, Mr. James",
 "fare" : 8.45829963684082,
 "parch" : 0,
 "ticket" : "330877",
 "sex" : "male",
 "passengerID" : 6,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "Q",
 "survived" : 0
 },
 {
 "name" : "McCarthy, Mr. Timothy J",
 "fare" : 51.86249923706055,
 "parch" : 0,
 "age" : 54.0,
 "ticket" : "17463",
 "cabin" : "E46",
 "sex" : "male",
 "passengerID" : 7,
 "pclass" : 1,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Palsson, Master. Gosta Leonard",
 "fare" : 21.075000762939453,
 "parch" : 1,
 "age" : 2.0,
 "ticket" : "349909",
 "sex" : "male",
 "passengerID" : 8,
 "pclass" : 3,
 "sibsp" : 3,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)",
 "fare" : 11.133299827575684,
 "parch" : 2,
 "age" : 27.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 9,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nasser, Mrs. Nicholas (Adele Achem)",
 "fare" : 30.07080078125,
 "parch" : 0,
 "age" : 14.0,
 "ticket" : "237736",
 "sex" : "female",
 "passengerID" : 10,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Sandstrom, Miss. Marguerite Rut",
 "fare" : 16.700000762939453,
 "parch" : 1,
 "age" : 4.0,
 "ticket" : "PP 9549",
 "cabin" : "G6",
 "sex" : "female",
 "passengerID" : 11,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Bonnell, Miss. Elizabeth",
 "fare" : 26.549999237060547,
 "parch" : 0,
 "age" : 58.0,
 "ticket" : "113783",
 "cabin" : "C103",
 "sex" : "female",
 "passengerID" : 12,
 "pcla

In [16]:
val nrClasses= 4
val sortedtrain= train.filter(x=>x.get("age")!=None).
               sortBy(x=>x("age").asInstanceOf[Float]) 
val sizeSet= sortedtrain.size
val sizeIntervals= sizeSet/nrClasses
val intervals= for (x <- 1 to nrClasses-1) yield 
              sortedtrain(x*sizeIntervals)("age").asInstanceOf[Float]
val newTrain= for(pass <- sortedtrain) yield pass.updated("ageclass",intervals.filter(_<pass("age").asInstanceOf[Float]).size)

Vegas("Age Distribution splitted by Calculated Intervals").
    withData(newTrain).
    addTransform("survival", "datum.survived == 0 ? \"No\" : \"Yes\"").
    mark(Bar).
    encodeX("ageclass", Ord).
    encodeY("passengerID", Quantitative ,AggOps.Count,axis=Axis(title="Passengers")).
    encodeColor("survival", Nominal, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA"))).
    show

<iframe id="frame-vegas-95a5ac2e-feea-493f-a9c9-7eea543a86df" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-95a5ac2e-feea-493f-a9c9-7eea543a86df'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "ageclass",
 "type" : "ordinal"
 },
 "y" : {
 "axis" : {
 "title" : "Passengers"
 },
 "field" : "passengerID",
 "type" : "quantitative",
 "aggregate" : "count"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "survival",
 "type" : "nominal"
 }
 },
 "description" : "Age Distribution splitted by Calculated Intervals",
 "data" : {
 "values" : [
 {
 "name" : "Thomas, Master. Assad Alexander",
 "ageclass" : 0,
 "fare" : 8.51669979095459,
 "parch" : 1,
 "age" : 0.41999998688697815,
 "ticket" : "2625",
 "sex" : "male",
 "passengerID" : 804,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Hamalainen, Master. Viljo",
 "ageclass" : 0,
 "fare" : 14.5,
 "parch" : 1,
 "age" : 0.6700000166893005,
 "ticket" : "250649",
 "sex" : "male",
 "passengerID" : 756,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Baclini, Miss. Helene Barbara",
 "ageclass" : 0,
 "fare" : 19.25830078125,
 "parch" : 1,
 "age" : 0.75,
 "ticket" : "2666",
 "sex" : "female",
 "passengerID" : 470,
 "pclass" : 3,
 "sibsp" : 2,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Baclini, Miss. Eugenie",
 "ageclass" : 0,
 "fare" : 19.25830078125,
 "parch" : 1,
 "age" : 0.75,
 "ticket" : "2666",
 "sex" : "female",
 "passengerID" : 645,
 "pclass" : 3,
 "sibsp" : 2,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Caldwell, Master. Alden Gates",
 "ageclass" : 0,
 "fare" : 29.0,
 "parch" : 2,
 "age" : 0.8299999833106995,
 "ticket" : "248738",
 "sex" : "male",
 "passengerID" : 79,
 "pclass" : 2,
 "sibsp" : 0,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Richards, Master. George Sibley",
 "ageclass" : 0,
 "fare" : 18.75,
 "parch" : 1,
 "age" : 0.8299999833106995,
 "ticket" : "29106",
 "sex" : "male",
 "passengerID" : 832,
 "pclass" : 2,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Allison, Master. Hudson Trevor",
 "ageclass" : 0,
 "fare" : 151.5500030517578,
 "parch" : 2,
 "age" : 0.9200000166893005,
 "ticket" : "113781",
 "cabin" : "C22 C26",
 "sex" : "male",
 "passengerID" : 306,
 "pclass" : 1,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Panula, Master. Eino Viljami",
 "ageclass" : 0,
 "fare" : 39.6875,
 "parch" : 1,
 "age" : 1.0,
 "ticket" : "3101295",
 "sex" : "male",
 "passengerID" : 165,
 "pclass" : 3,
 "sibsp" : 4,
 "embarked" : "S",
 "survived" : 0
 },
 {
 "name" : "Johnson, Miss. Eleanor Ileen",
 "ageclass" : 0,
 "fare" : 11.133299827575684,
 "parch" : 1,
 "age" : 1.0,
 "ticket" : "347742",
 "sex" : "female",
 "passengerID" : 173,
 "pclass" : 3,
 "sibsp" : 1,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Becker, Master. Richard F",
 "ageclass" : 0,
 "fare" : 39.0,
 "parch" : 1,
 "age" : 1.0,
 "ticket" : "230136",
 "cabin" : "F4",
 "sex" : "male",
 "passengerID" : 184,
 "pclass" : 2,
 "sibsp" : 2,
 "embarked" : "S",
 "survived" : 1
 },
 {
 "name" : "Nakid, Miss. Maria (\"\"Mary\"\")",
 "ageclass" : 0,
 "fare" : 15.741700172424316,
 "parch" : 2,
 "age" : 1.0,
 "ticket" : "2653",
 "sex" : "female",
 "passengerID" : 382,
 "pclass" : 3,
 "sibsp" : 0,
 "embarked" : "C",
 "survived" : 1
 },
 {
 "name" : "Goodwin, Master. Sidney Leonar

nrClasses: Int = 4
sortedtrain: List[Map[String, Any]] = List(
  Map(
    "name" -> "Thomas, Master. Assad Alexander",
    "fare" -> 8.5167F,
    "parch" -> 1,
    "age" -> 0.42F,
    "ticket" -> "2625",
    "sex" -> "male",
    "passengerID" -> 804,
    "pclass" -> 3,
    "sibsp" -> 0,
    "embarked" -> 'C',
    "survived" -> 1
  ),
  Map(
    "name" -> "Hamalainen, Master. Viljo",
    "fare" -> 14.5F,
    "parch" -> 1,
    "age" -> 0.67F,
    "ticket" -> "250649",
    "sex" -> "male",
    "passengerID" -> 756,
    "pclass" -> 2,
    "sibsp" -> 1,
    "embarked" -> 'S',
    "survived" -> 1
  ),
  Map(
    "name" -> "Baclini, Miss. Helene Barbara",
    "fare" -> 19.2583F,
    "parch" -> 1,
    "age" -> 0.75F,
    "ticket" -> "2666",
    "sex" -> "female",
    "passengerID" -> 470,
    "pclass" -> 3,
    "sibsp" -> 2,
    "embarked" -> 'C',
    "survived" -> 1
...
sizeSet: Int = 714
sizeIntervals: Int = 178
intervals: collection.immutable.IndexedSeq[Float] = Vector(20.0F, 28.0F, 38.0F)


In [17]:
def findInterval(attributeName: String, inputData: List[Map[String, Any]]) : List[Double] ={
    val max = inputData.filter(x => x.contains(attributeName)).map( y=> y(attributeName).toString.toDouble).max
    val min = inputData.filter(x => x.contains(attributeName)).map( y=> y(attributeName).toString.toDouble).min

    List(min, max)
  }

defined function findInterval

In [18]:
import java.util.concurrent.ThreadLocalRandom
//use random boolien to flag if you want to generate a random Value or use the one passed in method signature [true = use random; false = use valueToBeAssigned]
def fillEmptyEntries(missingKey: String, valueToBeAssigned: Any, originalData: List[Map[String, Any]], useRandomValue: Boolean): List[Map[String, Any]] = {

    val intervall = findInterval(missingKey, originalData)
    val min = intervall(0)
    val max = intervall(1)

    val random: ThreadLocalRandom = ThreadLocalRandom.current()

    val withKey = originalData.filter(x => x.contains( missingKey ))
    //1) getting all maps that do NOT contain the age key
    val withoutKey = originalData diff withKey
    //2) adding the age(Key) and assign avg_age(value) to those maps
    val withAddedKey = withoutKey.map( x => x + ( missingKey -> (if (! useRandomValue) {
      valueToBeAssigned
    } else {
      random.nextDouble(min, max + 1)
    })))
    //3) merging both Lists[Maps[String, Any]]
    (withKey ++ withAddedKey).sortBy(_("passengerID").toString.toInt)  //src: https://stackoverflow.com/questions/29672800/how-to-sort-a-list-of-maps-in-scala
  }

import java.util.concurrent.ThreadLocalRandom
//use random boolien to flag if you want to generate a random Value or use the one passed in method signature [true = use random; false = use valueToBeAssigned]

defined function fillEmptyEntries

In [19]:
 //precondition: no missing keys in inputdata
  def categorize(key: String, inputData : List[Map[String, Any]], categorizeFunction: (Any) => Any ) : List[Map[String, Any]] ={
    inputData.map(x => x + (key -> categorizeFunction(x(key))))
  }


defined function categorize

In [20]:
 def categorizeAge(age: Any): Any = {
    age match {
      case child      if (age.toString.toDouble <= 12.0) => "child"
      case adolescent if (age.toString.toDouble > 12.0 && age.toString.toDouble <= 18.0) => "adolescent"
      case adult      if (age.toString.toDouble > 18.0 && age.toString.toDouble <= 67.0) => "adult"
      case senior     if (age.toString.toDouble > 67.0) => "senior"
    }
  }



defined function categorizeAge

In [21]:
def categorizeParentsAndChildren(parch: Any): Any = {
    parch match {
      case none         if (parch.toString.toInt == 0) => "no family members"
      case oneToTwo     if (parch.toString.toInt > 0 && parch.toString.toInt <= 2) => "one or two family members"
      case moreThanTwo  if (parch.toString.toInt > 2) => "at least three family members"
    }
  }
 

defined function categorizeParentsAndChildren

In [22]:
def categorizeSiblingsOrSpouses(sibSp: Any): Any = {
    sibSp match {
      case none         if (sibSp.toString.toInt == 0) => "no sibling or spouse"
      case oneToTwo     if (sibSp.toString.toInt > 0 && sibSp.toString.toInt <= 2) => "one or two siblings/spouse"
      case moreThanTwo  if (sibSp.toString.toInt > 2) => "more than two siblings/spouse"
    }
  }


defined function categorizeSiblingsOrSpouses

In [23]:
def condProb(classAttribute: String,
               classAttributesValue: Any,

               conditionAttribute: String,
               conditionValue: Any,

               inputData: List[Map[String, Any]]): Double = {

    //count occurrence of conditionAttribute
    val listOfConditionOccurrence = inputData.filter(y => y(conditionAttribute) == conditionValue)
    val countOfConditionOccurrence = listOfConditionOccurrence.length

    //count occurrence of classAttribute WITHIN set that have conditionAttribute
    val countOfMatches = listOfConditionOccurrence.count(x => x(classAttribute) == classAttributesValue)
    //print(classAttribute, classAttributesValue, countOfMatches,"/", countOfConditionOccurrence, conditionAttribute, conditionValue, countOfConditionOccurrence, "/", inputData.length)
    countOfMatches.toDouble / countOfConditionOccurrence.toDouble
  }

defined function condProb

In [24]:
//use this for PriorProbabilities "how likely is it, given the fact you take a random dataentry to get sb with the conditions passed to the function?"
  def getPriorProbability(attributeName: String, attributeValue: Any, data: List[Map[String, Any]]): Double = {
    data.count(x => x(attributeName) == attributeValue) / data.flatMap(x => x.toList).count(y => y._1.equals(attributeName)).toDouble
  }


defined function getPriorProbability

In [26]:
//returns categories of possible values for given attribute
  def getCategories(attribute: String, data: List[Map[String, Any]]): List[Map[String, Any]] = {
    data.map(x => x.filter(y => y._1.equals(attribute))).distinct
  }

defined function getCategories

In [27]:
def selectData(listOfAttributes: List[String], inputData: List[Map[String, Any]]): List[Map[String, Any]] = {
    for (eachMapInInputData <- inputData) yield {
      listOfAttributes.map(x => x -> eachMapInInputData.getOrElse(x, "no Entry")).toMap
    }
  }


defined function selectData

In [28]:
def training(trainingData: List[Map[String, Any]],
               className: String, //"survived"
               listOfAttributes: List[String]):

  Map[(Any, Any), Double] = {

    val result = for (classValue <- getCategories(className, trainingData)) yield {
      for (attributeName <- listOfAttributes) yield {
        for (attributeValue <- getCategories(attributeName, trainingData)) yield {
          ((classValue(className), attributeValue(attributeName)), scala.math.log(condProb(className, classValue(className), attributeName, attributeValue(attributeName), trainingData))
          )
        } //survived -> value; sex, pclass ect.
      }
    }
    result.flatten.flatten.toMap
  }

defined function training

In [29]:
def classify( trainingData : List[Map[String, Any]],
                testData: List[Map[String, Any]],
                className: String,
                listOfAttributes: List[String]): //keys

  List[Any] = {

    //list of maps with All combinations of conditional probabilities
    //I AM A FAT MAP ((merkmal1, merkmal 2) -> cp)
    val cpOfTraining = training(trainingData, className, listOfAttributes) //key of these maps consists of attribute values

    // calc prior properties of className with each attribute (List[Map[valueOfgivenKey, pp]])
    val listOfPP = getCategories(className, trainingData).map(x => (x(className), getPriorProbability(className, x(className), trainingData))) //List[Map[1 -> pp ], Map[0 -> pp]]

    //contains a map for every dataSet with key value pairs
    val selectedData = selectData(listOfAttributes, testData) //list[Map[String,Any]]

    //===start calculation here
    /*
    1) find all matching attributes (e.g.) given one class (survived = 1) for given list of attributes

    example (attributelist contains "sex", "pclass") finde jetzt alle attribute für beide fälle (tot, überlebend), verrechne diese getrennt voneinander, gib den klasse der größeren von beiden zuürck
     */

    //i want to have List[Map[0 -> 0.9378465, 1 -> 0.077986345]]
    val result =
      for (dataSet <- selectedData) yield {
        for (classNamePP <- listOfPP) yield {
          Map( classNamePP._1 -> (
            for (eachAttribute <- listOfAttributes) yield {
              cpOfTraining(classNamePP._1, dataSet(eachAttribute))
            })).map(z => z._1 -> ((z._2.sum) + scala.math.log(classNamePP._2)))
        }
      }   //x = list containing maps with both attributeValues -> assignedLikelihood e.g. (0, -0.234183064587)
    result.map(x => x.flatten.toMap.maxBy(_._2)._1)
  }

defined function classify

In [30]:
def naiveBayes( trainingData: List[Map[String, Any]],
                  testData: List[Map[String, Any]],

                  className: String,

                  listOfAttributes: List[String]): // ("sex", "pclass", "fare")

  List[Any] = {

    //RUN FOREST RUN!
    classify(trainingData, testData, className, listOfAttributes)
  }

defined function naiveBayes

In [31]:
def mapResultWithID(result: List[Any], testData: List[Map[String, Any]]) : List[(Any, Any)] ={
    testData.map(x=> x("passengerID")).zip(result)
  }


defined function mapResultWithID

In [32]:
val train = loadDataCSV("train.csv")
    val test = loadDataCSV("test.csv")

    //replace missing entries with random / determined value
    val updatedTrain = fillEmptyEntries("age",0, train,true)
    val trainCategorizedAge = categorize("age", updatedTrain, categorizeAge)
    val trainCategorizedParch = categorize("parch", trainCategorizedAge, categorizeParentsAndChildren)
    val trainCategorizedAll = categorize("sibsp", trainCategorizedParch, categorizeSiblingsOrSpouses)


    val updatedTest = fillEmptyEntries("age",0,test,true)
    val testCategorizedAge = categorize("age", updatedTest, categorizeAge)
    val testCategorizedParch = categorize("parch", testCategorizedAge, categorizeParentsAndChildren)
    val testCategorizedAll = categorize("sibsp", testCategorizedParch, categorizeSiblingsOrSpouses)

    //For different calculations change listOfAttributes
    val listOfAttributes = List("sex","pclass", "age")
    //val listOfAttributes_2 = List("sex", "age")                                 //this one returns best prediction!!!
    //val listOfAttributes_3 = List("sex","pclass", "age", "parch", "sibsp")

    //val result = Utils.mapResultWithID(Utils.naiveBayes(trainCategorizedAll, testCategorizedAll,"survived", listOfAttributes), test)
    val result = naiveBayes(trainCategorizedAll, testCategorizedAll, "survived", listOfAttributes)
    //Utils.createSubmitFile("gender_age_submission.csv",result,"passengerID, survived")
    print(result)

List(0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0,

train: List[Map[String, Any]] = List(
  Map(
    "name" -> "Braund, Mr. Owen Harris",
    "fare" -> 7.25F,
    "parch" -> 0,
    "age" -> 22.0F,
    "ticket" -> "A/5 21171",
    "sex" -> "male",
    "passengerID" -> 1,
    "pclass" -> 3,
    "sibsp" -> 1,
    "embarked" -> 'S',
    "survived" -> 0
  ),
  Map(
    "name" -> "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
    "fare" -> 71.2833F,
    "parch" -> 0,
    "age" -> 38.0F,
    "ticket" -> "PC 17599",
    "cabin" -> "C85",
    "sex" -> "female",
    "passengerID" -> 2,
    "pclass" -> 1,
    "sibsp" -> 1,
    "embarked" -> 'C',
    "survived" -> 1
  ),
  Map(
    "name" -> "Heikkinen, Miss. Laina",
    "fare" -> 7.925F,
    "parch" -> 0,
    "age" -> 26.0F,
    "ticket" -> "STON/O2. 3101282",
    "sex" -> "female",
    "passengerID" -> 3,
    "pclass" -> 3,
    "sibsp" -> 0,
    "embarked" -> 'S',
...
test: List[Map[String, Any]] = List(
  Map(
    "name" -> "Kelly, Mr. James",
    "fare" -> 7.8292F,
    "parch" -> 0,
   

# Test

In [42]:
val train = loadDataCSV("train.csv")
val test = loadDataCSV("test.csv")
val all = train ++ test

val miniDataTRAINING = train.takeWhile(x => x("passengerID") != 16) // ~15 datasets
val miniDataTEST = test.takeWhile(x => x("passengerID") != 896)   

cmd42.sc:1: object scalatest is not a member of package org
import org.scalatest.FunSuite
           ^Compilation Failed

: 

In [34]:
assert(train.size == 891)
assert(test.size == 418)

In [55]:
val attList = List("passengerID", "pclass", "survived", "name", "sex", "age", "sibsp", "parch",
      "ticket", "fare", "cabin", "embarked")

countAllMissingValues(train, attList)

attList: List[String] = List(
  "passengerID",
  "pclass",
  "survived",
  "name",
  "sex",
  "age",
  "sibsp",
  "parch",
  "ticket",
  "fare",
  "cabin",
  "embarked"
)
res54_1: Map[String, Int] = Map(
  "name" -> 0,
  "fare" -> 0,
  "parch" -> 0,
  "age" -> 177,
  "ticket" -> 0,
  "cabin" -> 687,
  "sex" -> 0,
  "passengerID" -> 0,
  "pclass" -> 0,
  "sibsp" -> 0,
  "embarked" -> 2,
  "survived" -> 0
)

In [37]:
val attList = List("passengerID", "pclass", "survived", "name", "sex", "age", "sibsp", "parch",
      "ticket", "fare", "cabin", "embarked")

val train_mv = countAllMissingValues(train, attList)
val test_mv = countAllMissingValues(test, attList)
assert(train_mv("cabin") == 687 && train_mv("age") == 177 && train_mv("embarked") == 2)
assert(test_mv("cabin") == 327 && test_mv("age") == 86 && test_mv("fare") == 1)

attList: List[String] = List(
  "passengerID",
  "pclass",
  "survived",
  "name",
  "sex",
  "age",
  "sibsp",
  "parch",
  "ticket",
  "fare",
  "cabin",
  "embarked"
)
train_mv: Map[String, Int] = Map(
  "name" -> 0,
  "fare" -> 0,
  "parch" -> 0,
  "age" -> 177,
  "ticket" -> 0,
  "cabin" -> 687,
  "sex" -> 0,
  "passengerID" -> 0,
  "pclass" -> 0,
  "sibsp" -> 0,
  "embarked" -> 2,
  "survived" -> 0
)
test_mv: Map[String, Int] = Map(
  "name" -> 0,
  "fare" -> 1,
  "parch" -> 0,
  "age" -> 86,
  "ticket" -> 0,
  "cabin" -> 327,
  "sex" -> 0,
  "passengerID" -> 0,
  "pclass" -> 0,
  "sibsp" -> 0,
  "embarked" -> 0,
  "survived" -> 0
)

In [63]:
val attList = List("passengerID", "pclass", "survived", "name", "sex", "age", "sibsp", "parch",
      "ticket", "fare", "cabin", "embarked")

val train_mv = countAllMissingValues(train, attList)
val filledList = fillEmptyEntries("age", 9001, train, false)

//original dataset contains 177 entries with missing age attribute, filledList doesn't contain age as missing key-value-pair :)
assert(0 == (countAllMissingValues(filledList, List("age"))("age")))

attList: List[String] = List(
  "passengerID",
  "pclass",
  "survived",
  "name",
  "sex",
  "age",
  "sibsp",
  "parch",
  "ticket",
  "fare",
  "cabin",
  "embarked"
)
train_mv: Map[String, Int] = Map(
  "name" -> 0,
  "fare" -> 0,
  "parch" -> 0,
  "age" -> 177,
  "ticket" -> 0,
  "cabin" -> 687,
  "sex" -> 0,
  "passengerID" -> 0,
  "pclass" -> 0,
  "sibsp" -> 0,
  "embarked" -> 2,
  "survived" -> 0
)
filledList: List[Map[String, Any]] = List(
  Map(
    "name" -> "Braund, Mr. Owen Harris",
    "fare" -> 7.25F,
    "parch" -> 0,
    "age" -> 22.0F,
    "ticket" -> "A/5 21171",
    "sex" -> "male",
    "passengerID" -> 1,
    "pclass" -> 3,
    "sibsp" -> 1,
    "embarked" -> 'S',
    "survived" -> 0
  ),
  Map(
    "name" -> "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
    "fare" -> 71.2833F,
    "parch" -> 0,
    "age" -> 38.0F,
    "ticket" -> "PC 17599",
    "cabin" -> "C85",
    "sex" -> "female",
    "passengerID" -> 2,
    "pclass" -> 1,
    "sibsp" -> 1,
    "emba

In [64]:
val attList = List("passengerID", "pclass", "survived", "name", "sex", "age", "sibsp", "parch",
      "ticket", "fare", "cabin", "embarked")

    val train_mv = countAllMissingValues(train, attList)
    val filledList = fillEmptyEntries("age", 0, train, true)
   

    //original dataset contains 177 entries with missing age attribute, filledList doesn't contain age as missing key-value-pair :)
    assert(0 == (countAllMissingValues(filledList, List("age"))("age")))

attList: List[String] = List(
  "passengerID",
  "pclass",
  "survived",
  "name",
  "sex",
  "age",
  "sibsp",
  "parch",
  "ticket",
  "fare",
  "cabin",
  "embarked"
)
train_mv: Map[String, Int] = Map(
  "name" -> 0,
  "fare" -> 0,
  "parch" -> 0,
  "age" -> 177,
  "ticket" -> 0,
  "cabin" -> 687,
  "sex" -> 0,
  "passengerID" -> 0,
  "pclass" -> 0,
  "sibsp" -> 0,
  "embarked" -> 2,
  "survived" -> 0
)
filledList: List[Map[String, Any]] = List(
  Map(
    "name" -> "Braund, Mr. Owen Harris",
    "fare" -> 7.25F,
    "parch" -> 0,
    "age" -> 22.0F,
    "ticket" -> "A/5 21171",
    "sex" -> "male",
    "passengerID" -> 1,
    "pclass" -> 3,
    "sibsp" -> 1,
    "embarked" -> 'S',
    "survived" -> 0
  ),
  Map(
    "name" -> "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
    "fare" -> 71.2833F,
    "parch" -> 0,
    "age" -> 38.0F,
    "ticket" -> "PC 17599",
    "cabin" -> "C85",
    "sex" -> "female",
    "passengerID" -> 2,
    "pclass" -> 1,
    "sibsp" -> 1,
    "emba

In [65]:
assert(condProb("survived", 1, "sex", "female", train) +
    condProb("survived", 0, "sex", "female", train) == 1)

assert(condProb("survived", 1, "sex", "male", train) +
    condProb("survived", 0, "sex", "male", train) == 1)

assert(condProb("survived", 1, "pclass", 1, train) +
    condProb("survived", 0, "pclass", 1, train) == 1)

assert(condProb("survived", 1, "pclass", 2, train) +
    condProb("survived", 0, "pclass", 2, train) == 1)

assert(condProb("survived", 1, "pclass", 3, train) +
    condProb("survived", 0, "pclass", 3, train) == 1)

In [66]:
val trueValue = condProb("survived", 1, "sex", "female", train)

assert(condProb("survived", 1, "sex", "female", train) <= trueValue + 0.0000000001 &&
    condProb("survived", 1, "sex", "female", train) >= trueValue - 0.0000000001)

trueValue: Double = 0.7420382165605095

In [67]:
assert(BigDecimal(getPriorProbability("survived", 1, train)).setScale(3, BigDecimal.RoundingMode.HALF_UP) == 0.384)

In [68]:
assert(getCategories("survived", train) == List(Map("survived" -> 0), Map("survived" -> 1)))

In [69]:
assert(selectData(List("survived"), train).distinct == List(Map("survived" -> 0), Map("survived" -> 1)))

In [70]:
 assert(classify(miniDataTRAINING, miniDataTRAINING, "survived", List("sex", "pclass")) ==
      List(0, 1, 1, 1, 0, 0, 0, 0, 1, 1, 1, 1, 0, 0, 1))

In [71]:
assert(findInterval("age", train) == List(0.42, 80.0))

In [72]:
 val filledList = fillEmptyEntries("age", 0, train, true)

    def categorizeAge(age: Any): Any ={
      age match {
        case child      if (age.toString.toDouble <= 12.0) => "child"
        case adolescent if (age.toString.toDouble > 12.0 && age.toString.toDouble <= 18.0) => "adolescent"
        case adult      if (age.toString.toDouble > 18.0 && age.toString.toDouble <= 67.0) => "adult"
        case senior     if (age.toString.toDouble > 67.0) => "senior"
      }
    }

    val categorizedData = categorize("age", filledList, categorizeAge)

    val numberOfCategorizesEntries =
      categorizedData.count(x => x("age") == "child")       +
      categorizedData.count(x => x("age") == "adolescent")  +
      categorizedData.count(x => x("age") == "adult")       +
      categorizedData.count(x => x("age") == "senior")

    assert(numberOfCategorizesEntries == train.length)

filledList: List[Map[String, Any]] = List(
  Map(
    "name" -> "Braund, Mr. Owen Harris",
    "fare" -> 7.25F,
    "parch" -> 0,
    "age" -> 22.0F,
    "ticket" -> "A/5 21171",
    "sex" -> "male",
    "passengerID" -> 1,
    "pclass" -> 3,
    "sibsp" -> 1,
    "embarked" -> 'S',
    "survived" -> 0
  ),
  Map(
    "name" -> "Cumings, Mrs. John Bradley (Florence Briggs Thayer)",
    "fare" -> 71.2833F,
    "parch" -> 0,
    "age" -> 38.0F,
    "ticket" -> "PC 17599",
    "cabin" -> "C85",
    "sex" -> "female",
    "passengerID" -> 2,
    "pclass" -> 1,
    "sibsp" -> 1,
    "embarked" -> 'C',
    "survived" -> 1
  ),
  Map(
    "name" -> "Heikkinen, Miss. Laina",
    "fare" -> 7.925F,
    "parch" -> 0,
    "age" -> 26.0F,
    "ticket" -> "STON/O2. 3101282",
    "sex" -> "female",
    "passengerID" -> 3,
    "pclass" -> 3,
    "sibsp" -> 0,
    "embarked" -> 'S',
...
defined function categorizeAge
categorizedData: List[Map[String, Any]] = List(
  Map(
    "name" -> "Braund, Mr. Owen

In [73]:
assert(mapResultWithID(naiveBayes(miniDataTRAINING, miniDataTEST, "survived", List("sex", "pclass")), miniDataTEST) ==
      List((892,0), (893,1), (894,0), (895,0)))